In [5]:
import torch
import yaml
import os

# Humandoid MARL
from Humanoid_MARL.envs.base_env import GymWrapper, VectorGymWrapper
from Humanoid_MARL.utils.torch_utils import save_models, load_models
from Humanoid_MARL.agent.ppo.train_torch import Agent, eval_unroll, get_agent_actions
from Humanoid_MARL.envs.torch_wrapper import TorchWrapper
from IPython.display import HTML, clear_output
from brax.io import html
import jax
from Humanoid_MARL import envs
from Humanoid_MARL.utils.utils import load_reward_config, load_config

In [6]:
env_name = "ants"
config = load_config(env_name)
env = envs.create(config['env_name'], auto_reset=True, **config['env_config'])
env = GymWrapper(env, get_jax_state=True)
env = TorchWrapper(env, device=config['train_config']['device'], get_jax_state=True)

model = "models/20240405_204143_ppo_ants.pt"

model_path = os.path.join("../", model)
# env warmup
observation = env.reset()
action = torch.zeros(env.action_space.shape[0] * env.num_agents).to(config['train_config']['device'])
env.step(action)
agents = load_models(model_path, Agent, device=config['train_config']['device'])
jax_states = []
num_steps = 1000

eval_reward = 0.0
episodes = torch.zeros((), device = config['train_config']['device'])
for i in range(num_steps):
    print(f"{i} / {num_steps}")
    logits, action = get_agent_actions(agents, observation, env.obs_dims)
    if config['agent_config'].get("freeze_idx"):
        action[:,config['agent_config'].get("freeze_idx") * 8:(config['agent_config'].get("freeze_idx") * 8) + 8] =  torch.ones_like(action[:,config['agent_config'].get("freeze_idx") * 8:(config['agent_config'].get("freeze_idx") * 8) + 8]) * 0
    jax_state, observation, reward, done, info = env.step(Agent.dist_postprocess(action[0]))
    episodes += torch.sum(done)
    jax_states.append(jax_state)
    print(f"{i} | {info} | DONE [{done}] | Reward [{reward}]")
    eval_reward += reward
    if done:
        observation = env.reset()
        print(f"Episode Done")
        print(f"Total Reward | {eval_reward / episodes}")
print(f"Total Reward | {eval_reward / episodes}")

Models loaded from ../models/20240405_204143_ppo_ants.pt
0 / 1000
0 | {'distance_from_origin': tensor([0.2749, 3.0452], device='cuda:0'), 'first_obs': tensor([ 2.3871e-01,  1.2388e-01,  5.2283e-01,  4.1802e-01,  3.5103e-01,
         5.2903e-01,  6.0513e-01,  5.7181e-01,  5.3462e-01,  1.1692e-02,
         3.0261e-01,  5.4036e-01, -2.2878e-01,  4.6284e-01,  5.5735e-01,
         5.9392e-02, -1.0327e-01,  5.1663e-01, -1.2366e-01, -3.2743e-01,
         5.1072e-01,  4.6572e-01, -5.4854e-02,  5.0530e-01,  6.9888e-01,
        -2.2553e-01,  4.8800e-01,  3.0579e+00,  5.7454e-03,  5.8740e-01,
         3.2841e+00,  2.3135e-01,  5.9735e-01,  3.5302e+00,  4.3537e-01,
         6.0025e-01,  2.8367e+00,  2.2423e-01,  6.6176e-01,  2.5991e+00,
         4.2503e-01,  7.3515e-01,  2.8317e+00, -2.1986e-01,  5.7745e-01,
         2.5880e+00, -4.2665e-01,  5.7368e-01,  3.2791e+00, -2.1274e-01,
         5.1305e-01,  3.4917e+00, -4.3938e-01,  4.3838e-01,  9.4360e-03,
         2.0207e-02,  1.3057e-01,  5.9026e-03,

In [7]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

In [8]:
HTML(html.render(env.sys, [jax_state.pipeline_state for jax_state in jax_states])) 

: 